# 老上海影像修复




## 一、老视频修复简介

图像修复（英语：Inpainting）指重建的图像和视频中丢失或损坏的部分的过程。例如在博物馆中，这项工作常由经验丰富的博物馆管理员或者艺术品修复师来进行。数码世界中，图像修复又称图像插值或视频插值，指利用复杂的算法来替换已丢失、损坏的图像数据，主要替换一些小区域和瑕疵。

图像修复技术有许多目标和应用。
摄影和电影业中，使用这一技术来修复电影、还原变质恶化的胶片。同时，还可用来消除红眼、照片上的日期、水印等等，甚至还可以实现某些特效。
数字图像的编码和传输过程中也能使用图像修复技术替换丢失的数据。


### 安装PaddleGAN

PaddleGAN的安装目前支持Clone GitHub和Gitee两种方式：

In [7]:
# 安装ppgan
# 当前目录在: /home/aistudio/, 这个目录也是左边文件和文件夹所在的目录
# 克隆最新的PaddleGAN仓库到当前目录
# !git clone https://github.com/PaddlePaddle/PaddleGAN.git
# 如果从github下载慢可以从gitee clone：
!git clone https://gitee.com/paddlepaddle/PaddleGAN.git
%cd /home/aistudio/PaddleGAN/
!pip install -v -e .
!git checkout develop

fatal: destination path 'PaddleGAN' already exists and is not an empty directory.
/home/aistudio/PaddleGAN
Using pip 21.3.1 from /opt/conda/envs/python35-paddle120-env/lib/python3.7/site-packages/pip (python 3.7)
Looking in indexes: https://pypi.tuna.tsinghua.edu.cn/simple
Obtaining file:///home/aistudio/PaddleGAN
  Running command python setup.py egg_info
  running egg_info
  creating /tmp/pip-pip-egg-info-xk4f3dgl/ppgan.egg-info
  writing /tmp/pip-pip-egg-info-xk4f3dgl/ppgan.egg-info/PKG-INFO
  writing dependency_links to /tmp/pip-pip-egg-info-xk4f3dgl/ppgan.egg-info/dependency_links.txt
  writing entry points to /tmp/pip-pip-egg-info-xk4f3dgl/ppgan.egg-info/entry_points.txt
  writing requirements to /tmp/pip-pip-egg-info-xk4f3dgl/ppgan.egg-info/requires.txt
  writing top-level names to /tmp/pip-pip-egg-info-xk4f3dgl/ppgan.egg-info/top_level.txt
  writing manifest file '/tmp/pip-pip-egg-info-xk4f3dgl/ppgan.egg-info/SOURCES.txt'
  adding license file 'LICENSE' (matched pattern 'LICEN[


## 二、PaddleGAN中要使用的预测模型介绍

1. 补帧模型DAIN
1. 上色模型DeOldifyPredictor
1. 上色模型DeepRemasterPredictor
1. 图像超分辨率模型RealSRPredictor
1. 视频超分辨率模型PPMSVSR
1. 视频超分辨率模型BasicVSR系列
1. 超分辨率模型EDVR

![](https://ai-studio-static-online.cdn.bcebos.com/c6a5e5bb6a834659853a0cc9eb7b8ed4ed17bd983c3b46a09edb4b82df8ef4c6)


### 1.补帧模型DAIN
DAIN 模型通过探索深度的信息来显式检测遮挡。并且开发了一个深度感知的流投影层来合成中间流。在视频补帧方面有较好的效果。
![](./imgs/dain_network.png)

```
ppgan.apps.DAINPredictor(
                        output_path='output',
                        weight_path=None,
                        time_step=None,
                        use_gpu=True,
                        remove_duplicates=False)
```
#### 参数

- `output_path (str，可选的)`: 输出的文件夹路径，默认值：`output`.
- `weight_path (None，可选的)`: 载入的权重路径，如果没有设置，则从云端下载默认的权重到本地。默认值：`None`。
- `time_step (int)`: 补帧的时间系数，如果设置为0.5，则原先为每秒30帧的视频，补帧后变为每秒60帧。
- `remove_duplicates (bool，可选的)`: 是否删除重复帧，默认值：`False`.

### 2.上色模型DeOldifyPredictor
DeOldify 采用自注意力机制的生成对抗网络，生成器是一个U-NET结构的网络。在图像的上色方面有着较好的效果。
![](./imgs/deoldify_network.png)

```
ppgan.apps.DeOldifyPredictor(output='output', weight_path=None, render_factor=32)
```
#### 参数

- `output_path (str，可选的)`: 输出的文件夹路径，默认值：`output`.
- `weight_path (None，可选的)`: 载入的权重路径，如果没有设置，则从云端下载默认的权重到本地。默认值：`None`。
- `render_factor (int)`: 会将该参数乘以16后作为输入帧的resize的值，如果该值设置为32，
                         则输入帧会resize到(32 * 16, 32 * 16)的尺寸再输入到网络中。

### 3.上色模型DeepRemasterPredictor
DeepRemaster 模型基于时空卷积神经网络和自注意力机制。并且能够根据输入的任意数量的参考帧对图片进行上色。
![](./imgs/remaster_network.png)

```
ppgan.apps.DeepRemasterPredictor(
                                output='output',
                                weight_path=None,
                                colorization=False,
                                reference_dir=None,
                                mindim=360):
```
#### 参数

- `output_path (str，可选的)`: 输出的文件夹路径，默认值：`output`.
- `weight_path (None，可选的)`: 载入的权重路径，如果没有设置，则从云端下载默认的权重到本地。默认值：`None`。
- `colorization (bool)`: 是否对输入视频上色，如果选项设置为 `True` ，则参考帧的文件夹路径也必须要设置。默认值：`False`。
- `reference_dir (bool)`: 参考帧的文件夹路径。默认值：`None`。
- `mindim (bool)`: 输入帧重新resize后的短边的大小。默认值：360。

### 4.图像超分辨率模型RealSRPredictor
RealSR模型通过估计各种模糊内核以及实际噪声分布，为现实世界的图像设计一种新颖的真实图片降采样框架。基于该降采样框架，可以获取与真实世界图像共享同一域的低分辨率图像。并且提出了一个旨在提高感知度的真实世界超分辨率模型。对合成噪声数据和真实世界图像进行的大量实验表明，该模型能够有效降低了噪声并提高了视觉质量。

![](./imgs/realsr_network.png)

```
ppgan.apps.RealSRPredictor(output='output', weight_path=None)
```
#### 参数

- `output_path (str，可选的)`: 输出的文件夹路径，默认值：`output`.
- `weight_path (None，可选的)`: 载入的权重路径，如果没有设置，则从云端下载默认的权重到本地。默认值：`None`。

### 5.视频超分辨率模型PPMSVSR
百度自研的PP-MSVSR是一种多阶段视频超分深度架构，具有局部融合模块、辅助损失和细化对齐模块，以逐步细化增强结果。具体来说，在第一阶段设计了局部融合模块，在特征传播之前进行局部特征融合, 以加强特征传播中跨帧特征的融合。在第二阶段中引入了一个辅助损失，使传播模块获得的特征保留了更多与HR空间相关的信息。在第三阶段中引入了一个细化的对齐模块，以充分利用前一阶段传播模块的特征信息。大量实验证实，PP-MSVSR在Vid4数据集性能优异，仅使用 1.45M 参数PSNR指标即可达到28.13dB。

PP-MSVSR提供两种体积模型，开发者可根据实际场景灵活选择：PP-MSVSR（参数量1.45M）与PP-MSVSR-L（参数量7.42）。

![](./imgs/ppmsvsr_network.png)

```
ppgan.apps.PPMSVSRPredictor(output='output', weight_path=None, num_frames)
```
```
ppgan.apps.PPMSVSRLargePredictor(output='output', weight_path=None, num_frames)
```
#### 参数

- `output_path (str，可选的)`: 输出的文件夹路径，默认值：`output`.
- `weight_path (None，可选的)`: 载入的权重路径，如果没有设置，则从云端下载默认的权重到本地。默认值：`None`.
- `num_frames (int，可选的)`: 模型输入帧数，默认值：`10`.输入帧数越大，模型超分效果越好。

### 6.视频超分辨率模型BasicVSR系列
BasicVSR在VSR的指导下重新考虑了四个基本模块（即传播、对齐、聚合和上采样）的一些最重要的组件。 通过添加一些小设计，重用一些现有组件，得到了简洁的 BasicVSR。与许多最先进的算法相比，BasicVSR在速度和恢复质量方面实现了有吸引力的改进。 

同时，通过添加信息重新填充机制和耦合传播方案以促进信息聚合，BasicVSR 可以扩展为IconVSR，IconVSR可以作为未来 VSR 方法的强大基线 .

BasicVSR++通过提出二阶网格传播和导流可变形对齐来重新设计BasicVSR。通过增强传播和对齐来增强循环框架，BasicVSR++可以更有效地利用未对齐视频帧的时空信息。 在类似的计算约束下，新组件可提高性能。特别是，BasicVSR++ 以相似的参数数量在 PSNR 方面比 BasicVSR 高0.82dB。BasicVSR++ 在NTIRE2021的视频超分辨率和压缩视频增强挑战赛中获得三名冠军和一名亚军。

![](./imgs/basicvsr++_network.jpg)

```
ppgan.apps.BasicVSRPredictor(output='output', weight_path=None, num_frames)
```
```
ppgan.apps.IconVSRPredictor(output='output', weight_path=None, num_frames)
```
```
ppgan.apps.BasiVSRPlusPlusPredictor(output='output', weight_path=None, num_frames)
```
#### 参数

- `output_path (str，可选的)`: 输出的文件夹路径，默认值：`output`.
- `weight_path (None，可选的)`: 载入的权重路径，如果没有设置，则从云端下载默认的权重到本地。默认值：`None`.
- `num_frames (int，可选的)`: 模型输入帧数，默认值：`10`.输入帧数越大，模型超分效果越好。

### 7.超分辨率模型EDVR
EDVR模型提出了一个新颖的视频具有增强可变形卷积的还原框架：第一，为了处理大动作而设计的一个金字塔，级联和可变形（PCD）对齐模块，使用可变形卷积以从粗到精的方式在特征级别完成对齐；第二，提出时空注意力机制（TSA）融合模块，在时间和空间上都融合了注意机制，用以增强复原的功能。
![](./imgs/edvr_network.png)

```
ppgan.apps.EDVRPredictor(output='output', weight_path=None)
```
#### 参数

- `output_path (str，可选的)`: 输出的文件夹路径，默认值：`output`.
- `weight_path (None，可选的)`: 载入的权重路径，如果没有设置，则从云端下载默认的权重到本地。默认值：`None`。

### 二、使用PaddleGAN进行视频修复

####**** 导入包

In [8]:
# 导入一些可视化需要的包
import cv2
import imageio
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.animation as animation
from IPython.display import HTML
import warnings
warnings.filterwarnings("ignore")

#### 定义展示视频的函数

In [9]:
# 定义一个展示视频的函数
def display(driving, fps, size=(8, 6)):
    fig = plt.figure(figsize=size)

    ims = []
    for i in range(len(driving)):
        cols = []
        cols.append(driving[i])

        im = plt.imshow(np.concatenate(cols, axis=1), animated=True)
        plt.axis('off')
        ims.append([im])

    video = animation.ArtistAnimation(fig, ims, interval=1000.0/fps, repeat_delay=1000)

    plt.close()
    return video

#### 展示视频

In [10]:
# 展示一下输入的视频, 如果视频太大，时间会非常久，可以跳过这个步骤
video_path = '/home/aistudio/shanghai6.mp4'
video_frames = imageio.mimread(video_path, memtest=False)

# 获得视频的原分辨率
cap = cv2.VideoCapture(video_path)
fps = cap.get(cv2.CAP_PROP_FPS)
    

HTML(display(video_frames, fps).to_html5_video())

### 使用插帧(DAIN), 上色(DeOldify), 超分(MSVSR)这三个模型对该视频进行修复

In [11]:
# 使用插帧(DAIN), 上色(DeOldify), 超分(MSVSR)这三个模型对该视频进行修复
# input参数表示输入的视频路径
# output表示处理后的视频的存放文件夹
# proccess_order 表示使用的模型和顺序（目前支持）
# %cd applications/

%cd /home/aistudio/PaddleGAN/applications/

!python tools/video-enhance.py --input /home/aistudio/shanghai6.mp4 \
                               --process_order DAIN DeOldify PPMSVSR \
                               --output /home/aistudio/output_dir

/home/aistudio/PaddleGAN/applications
Model DAIN process start..
[02/21 21:09:53] ppgan INFO: Downloading DAIN_weight.tar from https://paddlegan.bj.bcebos.com/applications/DAIN_weight.tar to /home/aistudio/.cache/ppgan/DAIN_weight.tar
100%|██████████████████████████████████| 78680/78680 [00:02<00:00, 35118.50it/s]
[02/21 21:09:55] ppgan INFO: Decompressing /home/aistudio/.cache/ppgan/DAIN_weight.tar...
2022-02-21 21:09:55,730-WARNING: The old way to load inference model is deprecated. model path: /home/aistudio/.cache/ppgan/DAIN_weight/model, params path: /home/aistudio/.cache/ppgan/DAIN_weight/params
W0221 21:09:56.194197  1371 device_context.cc:404] Please NOTE: device: 0, GPU Compute Capability: 7.0, Driver API Version: 10.1, Runtime API Version: 10.1
W0221 21:09:56.199790  1371 device_context.cc:422] device: 0, cuDNN Version: 7.6.
Old fps (frame rate):  24.515722355565252
New fps (frame rate):  48
100%|███████████████████████████████████████████| 78/78 [01:11<00:00,  1.09it/s]
Mode

#### 展示处理好的视频

In [12]:
# 展示一下处理好的视频, 如果视频太大，时间会非常久，可以下载下来看
# 这个路径可以查看上个code cell的最后打印的output video path

output_video_path = '/home/aistudio/output_dir/PPMSVSR/shanghai6_deoldify_out_PPMSVSR_out.mp4'

video_frames = imageio.mimread(output_video_path, memtest=False)

# 获得视频的原分辨率
cap = cv2.VideoCapture(output_video_path)
fps = cap.get(cv2.CAP_PROP_FPS)
    

HTML(display(video_frames, fps, size=(16, 12)).to_html5_video())

### 展示下一个视频

In [13]:
# 展示一下输入的视频, 如果视频太大，时间会非常久，可以跳过这个步骤
# video_path = '/home/aistudio/011.mp4'
video_path = '/home/aistudio/shanghai7.mp4'

video_frames = imageio.mimread(video_path, memtest=False)

# 获得视频的原分辨率
cap = cv2.VideoCapture(video_path)
fps = cap.get(cv2.CAP_PROP_FPS)

print('fps:'+str(fps))

HTML(display(video_frames, fps).to_html5_video())

fps:24.469129423921466


#### PPMSVSR模型对该视频进行修复

In [15]:
# PPMSVSR模型对该视频进行修复
# input参数表示输入的视频路径
# output表示处理后的视频的存放文件夹
# proccess_order 表示使用的模型和顺序（目前支持）
# num_frames 表示模型输入帧数
%cd /home/aistudio/PaddleGAN/applications
!python tools/video-enhance.py --input /home/aistudio/shanghai7.mp4 \
                               --process_order PPMSVSR \
                               --output /home/aistudio/output_dir \
                               --num_frames 40

/home/aistudio/PaddleGAN/applications
Model PPMSVSR process start..
W0221 21:31:15.658663  3113 device_context.cc:404] Please NOTE: device: 0, GPU Compute Capability: 7.0, Driver API Version: 10.1, Runtime API Version: 10.1
W0221 21:31:15.663830  3113 device_context.cc:422] device: 0, cuDNN Version: 7.6.
/opt/conda/envs/python35-paddle120-env/lib/python3.7/site-packages/paddle/tensor/creation.py:125: DeprecationWarning: `np.object` is a deprecated alias for the builtin `object`. To silence this warning, use `object` by itself. Doing this will not modify any behavior and is safe. 
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  if data.dtype == np.object:
[02/21 21:31:20] ppgan INFO: Found /home/aistudio/.cache/ppgan/modified_spynet_tiny.pdparams
[02/21 21:31:20] ppgan INFO: Found /home/aistudio/.cache/ppgan/PP-MSVSR_reds_x4.pdparams
100%|█████████████████████████████████████████████| 2/2 [00:48<00:00, 24.06s/it

In [17]:
# 展示一下处理好的视频, 如果视频太大，时间会非常久，可以下载下来看
# 这个路径可以查看上个code cell的最后打印的output video path
output_video_path = '/home/aistudio/output_dir/PPMSVSR/shanghai7_PPMSVSR_out.mp4'

video_frames = imageio.mimread(output_video_path, memtest=False)

# 获得视频的原分辨率
cap = cv2.VideoCapture(output_video_path)
fps = cap.get(cv2.CAP_PROP_FPS)
    

HTML(display(video_frames, fps, size=(16, 12)).to_html5_video())

## 三、个人总结

非常优秀的模型，效率非常高，虽然效果上还没有达到理想的状态（能以假乱真的程度），但是目前能到到这个程度已是非常大的进步。
上色模型，相信会有更多的上色风格出现，例如：完全写实型（原汁原味）、艺术修饰性（在原汁原味的基础上，增加艺术修饰）等。